**Ejercicio 1 - Hapax**

Un hapax legomenon es un termino que proviene del griego, y hace referencia a una palabra que ocurre una única vez dentro de un contexto. Este contexto, queda definido muchas veces por el caso de estudio.

El objetivo de este ejercicio, es encontrar el Hapax dentro del corpus del Quijote de la Mancha. Deberán es aplicar algunas técnicas de limpieza de datos, y tokenización para poder ver si existe o no dentrodel Quijote, un hapax.

Como se dijo, hapax puede depender de contexto que se defina. Para este ejercicio, el contexto será:

El corpus completo.
Una unidad a elección del grupo.

In [1]:
#!pip install inflect

In [2]:
#!pip install contractions

In [3]:
import re, string, unicodedata
import nltk
#nltk.download('punkt')
#nltk.download('stopwords')
#import contractions
import inflect
from bs4 import BeautifulSoup
from nltk import word_tokenize, sent_tokenize
from nltk.corpus import stopwords
from nltk.stem import LancasterStemmer, WordNetLemmatizer
from collections import Counter

In [4]:
enc='utf-8'
all_quijote =[]
with open('./data/don_quijote.txt','r',encoding=enc) as f:
     #lines = f.readlines()
    for line in f:
        all_quijote.append(line)

In [5]:
#print(all_quijote)

In [6]:
limitedel = all_quijote.index('file corrections and new HTML file by Joaquin Cuenca Abela.\n')
print(limitedel)
posicion=0
while posicion<limitedel:
    all_quijote.pop(posicion)
    posicion=posicion+1

24


In [7]:
posicion = all_quijote.index("End of Project Gutenberg's Don Quijote, by Miguel de Cervantes Saavedra\n")
print(posicion)
print(len(all_quijote))
while posicion<len(all_quijote):
    all_quijote.pop(posicion)
    posicion=posicion+1

37474
37838


In [8]:
texto = ' '.join(all_quijote)
print(texto)


 almost no restrictions whatsoever.  You may copy it, give it away or
 with this eBook or online at www.gutenberg.net
 
 
 
 Release Date: December, 1999
 Language: Spanish
 
 
 
 Produced by an anonymous Project Gutenberg volunteer. Text
 
 
 
 
 
 
 
 TASA
 Yo, Juan Gallo de Andrada, escribano de Cámara del Rey nuestro señor, de
 los señores dél un libro intitulado El ingenioso hidalgo de la Mancha,
 libro a tres maravedís y medio; el cual tiene ochenta y tres pliegos, que
 en que se ha de vender en papel; y dieron licencia para que a este precio
 se pueda vender, y mandaron que esta tasa se ponga al principio del dicho
 libro, y no se pueda vender sin ella. Y, para que dello conste, di la
 presente en Valladolid, a veinte días del mes de deciembre de mil y
 seiscientos y cuatro años.
 
 Juan Gallo de Andrada.
 
 TESTIMONIO DE LAS ERRATAS
 
 Este libro no tiene cosa digna que no corresponda a su original; en
 testimonio de lo haber correcto, di esta fee. En el Colegio de la Madre de

In [9]:
#posicion = all_quijote.index('This and all associated files of various formats will be found in:')
#print(posicion)

##Data Preprocessing##
Esta formado por los siguientes pasos
1° Eliminacion de Ruidos
2° Tokenizacion
3° Normalizacion


In [10]:
#Funciones para eliminacion de ruidos
def strip_html(text):
    soup = BeautifulSoup(text, "html.parser")
    return soup.get_text()

def remove_between_square_brackets(text):
    return re.sub('\[[^]]*\]', '', text)

def denoise_text(text):
    text = strip_html(text)
    text = remove_between_square_brackets(text)
    return text

In [11]:
#1 - Eliminación de Ruidos
texto = denoise_text(texto)
#print(texto)

In [12]:
#2 - Tokenizacion
words = nltk.word_tokenize(texto)
print(words)


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [13]:
#Funciones de Normalizacion
def remove_non_ascii(words):
    """Remueve  caracteres non-ASCII de la lista tokenizeda words"""
    new_words = []
    for word in words:
        new_word = unicodedata.normalize('NFKD', word).encode('ascii', 'ignore').decode('utf-8', 'ignore')
        new_words.append(new_word)
    return new_words

def to_lowercase(words):
    """Convierte todos los caracteres a minuscula de la lista tokenizada words"""
    new_words = []
    for word in words:
        new_word = word.lower()
        new_words.append(new_word)
    return new_words

def remove_punctuation(words):
    """Remueve signos punctuacion de la lista tokenizada words"""
    new_words = []
    for word in words:
        new_word = re.sub(r'[^\w\s]', '', word)
        if new_word != '':
            new_words.append(new_word)
    return new_words

def replace_numbers(words):
    """Reemplaza todos los numeros por valores conceptualizados"""
    p = inflect.engine()
    new_words = []
    for word in words:
        if word.isdigit():
            new_word = p.number_to_words(word)
            new_words.append(new_word)
        else:
            new_words.append(word)
    return new_words

def remove_stopwords(words):
    """Remueve stop words de lista tokenizada words"""
    new_words = []
    for word in words:
        if word not in stopwords.words('spanish'): #english
            new_words.append(word)
    return new_words

def stem_words(words):
    """Stem words in list of tokenized words"""
    stemmer = LancasterStemmer()
    stems = []
    for word in words:
        stem = stemmer.stem(word)
        stems.append(stem)
    return stems

def lemmatize_verbs(words):
    """Lemmatize verbs in list of tokenized words"""
    lemmatizer = WordNetLemmatizer()
    lemmas = []
    for word in words:
        lemma = lemmatizer.lemmatize(word, pos='v')
        lemmas.append(lemma)
    return lemmas

def normalize(words):
    words = remove_non_ascii(words)
    words = to_lowercase(words)
    words = remove_punctuation(words)
    words = replace_numbers(words)
    words = remove_stopwords(words)
    return words


In [14]:
#3-Normalizacion
words = normalize(words)
print(words)

['almost', 'restrictions', 'whatsoever', 'you', 'may', 'copy', 'it', 'give', 'it', 'away', 'or', 'with', 'this', 'ebook', 'or', 'online', 'at', 'wwwgutenbergnet', 'release', 'date', 'december', 'one thousand, nine hundred and ninety-nine', 'language', 'spanish', 'produced', 'by', 'an', 'anonymous', 'project', 'gutenberg', 'volunteer', 'text', 'tasa', 'juan', 'gallo', 'andrada', 'escribano', 'camara', 'rey', 'senor', 'senores', 'libro', 'intitulado', 'ingenioso', 'hidalgo', 'mancha', 'libro', 'tres', 'maravedis', 'medio', 'ochenta', 'tres', 'pliegos', 'vender', 'papel', 'dieron', 'licencia', 'precio', 'pueda', 'vender', 'mandaron', 'tasa', 'ponga', 'principio', 'dicho', 'libro', 'pueda', 'vender', 'dello', 'conste', 'di', 'presente', 'valladolid', 'veinte', 'dias', 'mes', 'deciembre', 'mil', 'seiscientos', 'cuatro', 'anos', 'juan', 'gallo', 'andrada', 'testimonio', 'erratas', 'libro', 'cosa', 'digna', 'corresponda', 'original', 'testimonio', 'haber', 'correcto', 'di', 'fee', 'colegio', 

In [15]:
def stem_and_lemmatize(words):
    stems = stem_words(words)
    lemmas = lemmatize_verbs(words)
    return stems, lemmas

In [16]:
def word_form_hapaxes(words):
    counts = Counter(words) 
    hapaxes = [word for word in counts if counts[word] == 1] 
    return hapaxes

In [17]:
hapax = word_form_hapaxes(words)

In [18]:
print('Hapaxes: ',hapax)

Hapaxes:  ['release', 'december', 'one thousand, nine hundred and ninety-nine', 'language', 'spanish', 'anonymous', 'volunteer', 'text', 'conste', 'deciembre', 'correcto', 'diciembre', 'one thousand, six hundred and four', 'pedistes', 'previlegio', 'acusare', 'plana', 'tase', 'volume', 'sucesivamente', 'cualesquier', 'setiembre', 'amezqueta', 'gibraleon', 'benalcazar', 'banares', 'vizconde', 'puebla', 'alcocer', 'curiel', 'burguillos', 'mayormente', 'agradablemente', 'proteccion', 'ornamento', 'elegancia', 'continiendose', 'desdenara', 'cultivado', 'antojadizo', 'fecundas', 'colmen', 'suplicarte', 'perdones', 'esenta', 'calunien', 'premien', 'monda', 'ornato', 'inumerabilidad', 'componerla', 'prefacion', 'escribille', 'escribiria', 'imaginativo', 'encubriendosela', 'eruditos', 'citan', 'doctores', 'renglon', 'sermoncico', 'leelle', 'acotar', 'anotar', 'xenofonte', 'zoilo', 'zeuxis', 'marqueses', 'celeberrimos', 'igualasen', 'prosegui', 'adorne', 'insuficiencia', 'poltron', 'elevamiento